moving the county stuff here in the hope i can work out what is going on

In [1]:
from math import sqrt
import pandas as pd
import json
import requests
import random
import folium
from shapely.geometry import Point
from shapely.geometry import shape

In [39]:
geo_df = pd.read_csv('us-county-boundaries.csv', sep=';')
geo_df.head()

Geo Point  \
0  39.7847564917,-100.459899544   
1  38.4561871377,-96.1526397502   
2   43.560975208,-73.8460059552   
3  37.2372753377,-97.4765502094   
4   42.781081385,-76.8237785954   

                                           Geo Shape  STATEFP  COUNTYFP  \
0  {"type": "Polygon", "coordinates": [[[-100.740...       20        39   
1  {"type": "Polygon", "coordinates": [[[-96.3543...       20       111   
2  {"type": "Polygon", "coordinates": [[[-74.1825...       36       113   
3  {"type": "Polygon", "coordinates": [[[-97.8045...       20       191   
4  {"type": "Polygon", "coordinates": [[[-76.9635...       36        99   

   COUNTYNS  GEOID     NAME        NAMELSAD STUSAB  LSAD  ...  CSAFP   CBSAFP  \
0    484989  20039  Decatur  Decatur County     KS     6  ...    NaN      NaN   
1    485020  20111     Lyon     Lyon County     KS     6  ...    NaN  21380.0   
2    974154  36113   Warren   Warren County     NY     6  ...  104.0  24020.0   
3    481812  20191   Sumner   Sumner County     KS     6  ...  556.0  48620.0   
4    974147  36099   Seneca   Seneca County     NY     6  ...  464.0  42900.0   

   METDIVFP  FUNCSTAT       ALAND     AWATER   INTPTLAT    INTPTLON  \
0       NaN         A  2314199329    1631670  39.783542 -100.459708   
1       NaN         A  2194978406   20541643  38.455403  -96.161641   
2       NaN         A  2246082355  166754989  43.555105  -73.838139   
3       NaN         A  3060472194    8546399  37.236662  -97.493352   
4       NaN         A   838403628  172828921  42.782294  -76.827088   

   STATE_NAME  COUNTYFP NOZERO  
0      Kansas               39  
1      Kansas              111  
2    New York              113  
3      Kansas              191  
4    New York               99  

[5 rows x 22 columns]

In [40]:
geo_df = geo_df[['STATE_NAME', 'STUSAB', 'NAMELSAD', 'ALAND', 'AWATER', 'Geo Point', 'Geo Shape']]
geo_df['area'] = geo_df['ALAND'] + geo_df['AWATER']
geo_df.drop(['ALAND', 'AWATER'], axis=1, inplace=True)
geo_df.columns = ['state_name', 'state', 'county', 'Geo Point', 'Geo Shape', 'area']
geo_df.head()

geo_df["county"].is_unique

False

make random points


In [4]:
def generate_random(number, polygon):
    list_of_points = []
    minx, miny, maxx, maxy = polygon.bounds
    counter = 0
    while counter < number:
        pnt = Point(random.uniform(minx, maxx), random.uniform(miny, maxy))
        if polygon.contains(pnt):
            coords = pnt.coords.xy
            lat = coords[1][0]
            lng = coords[0][0]
            list_of_points.append([lat, lng])
            counter += 1
    return list_of_points

def get_points(df):
    points_list = []
    for index, row in df.iterrows():
        state = row['state']
        county = row['county']
        poly = shape(json.loads(row['Geo Shape']))

        number = int(sqrt(row['area'])/50000)
        if number == 0:
            number = 2

        list_of_points = generate_random(number, poly)
        points_list.append([state, county, list_of_points])

    return points_list

In [5]:
# trying it with the first one
points = get_points(geo_df[:1])
points, len(points[0][2])

([['KS',
   'Decatur County',
   [[39.85183439007632, -100.73630591773579],
    [39.67597552188234, -100.29254444565912]]]],
 2)

In [22]:
# let's try and put them in a df
df = pd.DataFrame(columns = ['state', 'county', 'latitude', 'longitude'])
for x in range(len(points)):
    coords =  points[x][2]
    for i in range(len(coords)):
        state = points[x][0]
        county = points[x][1]
        lat = (coords[i][0])
        lng = (coords[i][1])

        df = df.append({'state': state, 'county': county, 'latitude': lat, 'longitude': lng}, ignore_index=True)

df.head()

state          county   latitude   longitude
0    KS  Decatur County  39.851834 -100.736306
1    KS  Decatur County  39.675976 -100.292544

ok, i have points.
let's try and plot them and see where they are

In [23]:
test_map = folium.Map(location=[39.7480, -100.5296], zoom_start=8)

# add the county borders
folium.GeoJson('us-county-boundaries.geojson', name="geojson").add_to(test_map)

# plot the circles
things = folium.map.FeatureGroup()

for lat, lng, in zip(df['latitude'], df['longitude']):
    things.add_child(
        folium.Circle(radius=50000,
            location=[lat, lng],
            color='crimson',
            fill=False,
        )
    )

# add incidents to map
test_map.add_child(things)
test_map

perfect, they cover the county entirely. let's try and check for hospitals


In [31]:
# Foursquare credentials
with open('credentials.json') as f:
    creds = json.load(f)

    CLIENT_ID = creds[0]['CLIENT_ID']
    CLIENT_SECRET = creds[0]['CLIENT_SECRET']

VERSION =  "20200101"
LIMIT = 50

# categories
categoryID1 = '4bf58dd8d48988d196941735'  # hospitals
categoryID2 = '4bf58dd8d48988d177941735'  # doctor's offices
categoryID3 = '4d4b7105d754a06374d81259'  # food

radius = 50000

def get_hospitals2(states, counties, lats, lngs):
    hospital_list = []
    id_list = []
    for i in range(len(lats)):
        state = states[i]
        county = counties[i]
        lat = lats[i]
        lng = lngs[i]

        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/search?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&categoryId={}'.format(
            CLIENT_ID,
            CLIENT_SECRET,
            VERSION,
            lat,
            lng,
            radius,
            LIMIT,
            categoryID1
            )
        try:
            results = requests.get(url).json()["response"]['venues'][0]
            # print(results)

            # return only relevant information for each nearby venue
            if results['id'] not in id_list:
                id_list.append(results['id'])
                print(results['name'])  # so I don't panic!
                hospital_list.append([(
                state,
                county,
                results['name'],
                results['location']['lat'],
                results['location']['lng'],
                )])
        except KeyError:
            pass
    return hospital_list

In [32]:
hosps = get_hospitals2(df['state'], df['county'], df['latitude'], df['longitude'])
hosps

McCook Community Hospital
Sheridan County Health Complex


[[('KS',
   'Decatur County',
   'McCook Community Hospital',
   40.20512008666992,
   -100.60830688476562)],
 [('KS',
   'Decatur County',
   'Sheridan County Health Complex',
   39.35417741436831,
   -100.4325270652771)]]

ok, so
same starting coords get different results each time
this is fucking useless but it's what i have

In [33]:
# check they are in the county
for x in range(len(hosps)):
    state = hosps[x][0][0]
    county = hosps[x][0][1]
    hospital = hosps[x][0][2]
    latitude = hosps[x][0][3]
    longitude = hosps[x][0][4]

    point = Point(longitude, latitude)
    poly = geo_df[geo_df['county'] == county]['Geo Shape'].item()
    poly = shape(json.loads(poly))

    if poly.contains(point):
        print(county, hospital)
    else:
        print('no hospitals')


no hospitals
no hospitals


In [35]:
# put the coords in the df

df2 = pd.DataFrame(columns=['state', 'county', 'hospital', 'latitude', 'longitude'])

for x in range(len(hosps)):
    state = hosps[x][0][0]
    county = hosps[x][0][1]
    hospital = hosps[x][0][2]
    latitude = hosps[x][0][3]
    longitude = hosps[x][0][4]

    df2 = df2.append({'state': state, 'county': county, 'hospital': hospital, 'latitude': latitude, 'longitude': longitude}, ignore_index=True)

df2.drop_duplicates(subset=['latitude', 'longitude'], keep='last', inplace=True)
df2.head()

state          county                        hospital   latitude   longitude
0    KS  Decatur County       McCook Community Hospital  40.205120 -100.608307
1    KS  Decatur County  Sheridan County Health Complex  39.354177 -100.432527

In [37]:
df2.groupby('county').count()

state  hospital  latitude  longitude
county                                              
Decatur County      2         2         2          2